# Preparation Phase

In [1]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import current_timestamp
from pyspark.sql.types import DateType

import os
import csv
import glob
import time, timeit

import matplotlib.pyplot as plt
import numpy as np
import xml.etree.ElementTree as ET
import pandas as pd

from datetime import datetime
from decimal import Decimal
from scipy.stats import gmean

In [ ]:
# Time measure for preparation phase
start_time_prepa = time.time()

In [3]:
# Initialize SparkSession
spark = SparkSession.builder.appName("TPC-DS Data Loading").config("spark.jars.packages", "com.databricks:spark-xml_2.12:0.13.0").config("spark.sql.catalogImplementation", "hive").getOrCreate()
SF = 3 #choose between 3,5,8,10, 15

23/12/24 15:01:58 WARN Utils: Your hostname, alex-Lenovo-Legion-5-15IMH05H resolves to a loopback address: 127.0.1.1; using 192.168.1.40 instead (on interface wlp0s20f3)
23/12/24 15:01:58 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address


:: loading settings :: url = jar:file:/home/alex/.local/lib/python3.10/site-packages/pyspark/jars/ivy-2.5.1.jar!/org/apache/ivy/core/settings/ivysettings.xml


Ivy Default Cache set to: /home/alex/.ivy2/cache
The jars for the packages stored in: /home/alex/.ivy2/jars
com.databricks#spark-xml_2.12 added as a dependency
:: resolving dependencies :: org.apache.spark#spark-submit-parent-f770d0dc-5a52-4e92-aa1d-d28e86ad51e3;1.0
	confs: [default]
	found com.databricks#spark-xml_2.12;0.13.0 in central
	found commons-io#commons-io;2.8.0 in central
	found org.glassfish.jaxb#txw2;2.3.4 in central
	found org.apache.ws.xmlschema#xmlschema-core;2.2.5 in central
:: resolution report :: resolve 180ms :: artifacts dl 8ms
	:: modules in use:
	com.databricks#spark-xml_2.12;0.13.0 from central in [default]
	commons-io#commons-io;2.8.0 from central in [default]
	org.apache.ws.xmlschema#xmlschema-core;2.2.5 from central in [default]
	org.glassfish.jaxb#txw2;2.3.4 from central in [default]
	---------------------------------------------------------------------
	|                  |            modules            ||   artifacts   |
	|       conf       | number| searc

In [4]:
#order of table to load

Not_modified_table = [["Time", "DimTime"], ["Date", "DimDate"],["Industry", "Industry"],
                     ["StatusType", "StatusType"],["TaxRate", "TaxRate"],["TradeType","TradeType"]]

FINWIRE_table = [["FINWIRE","DimCompany"],["FINWIRE","DimSecurity"],["FINWIRE","Financial"]]

Modified_DimTable = [["CustomerMgmt.csv","DimCustomer"],["HR.csv","DimBroker"],
                         ["CustomerMgmt.csv","DimAccount"], ["Trade.txt","DimTrade"]] 


Modified_FactTable = [["CashTransaction.txt","FactCashBalances"],["HoldingHistory.txt","FactHoldings"]
                                  ,["DailyMarket.txt","FactMarketHistory"],["WatchHistory.txt","FactWatches"]
                                  ,["Prospect.csv","Prospect"]]

In [5]:
#How split FINWIRE FILES

cmp_colspecs=[(0, 15), (15, 18), (18, 78), (78, 88), (88, 92), (92, 94), (94, 98), (98, 106), (106, 186), (186, 266), (266, 278), (278, 303), (303, 323), (323, 347), (347, 393), (393, 543)]
fin_colspecs=[(0, 15), (15, 18), (18, 22), (22, 23), (23, 31), (31, 39), (39, 56), (56, 73), (73, 85), (85, 97), (97, 109), (109, 126), (126, 143), (143, 160), (160, 173), (173, 186), (186, 246)]
sec_colspecs=[(0, 15), (15, 18), (18, 33), (33, 39), (39, 43), (43, 113), (113, 119), (119, 132), (132, 140), (140, 148), (148, 160), (160, 220)]

In [6]:
# For DImessages

valid_ratings = ["AAA", "AA[+/-]", "A[+/-]", "BBB[+/-]", "BB[+/-]", "B[+/-]", "CCC[+/-]", "CC", "C", "D"]

In [7]:
"""f = open(os.getcwd() + "/ddl/tpcdi.sql", "r")
tables=f.read()
tables = tables.split(";")[1:-1]
for i in tables:
    spark.sql(i)
# If not done: create the audit table in tpcdi.sql"""

'f = open(os.getcwd() + "/ddl/tpcdi.sql", "r")\ntables=f.read()\ntables = tables.split(";")[1:-1]\nfor i in tables:\n    spark.sql(i)\n# If not done: create the audit table in tpcdi.sql'

In [8]:
# This function checks if more than 2 minutes and less than 5 minutes elapsed between two visibility
# queries execution. If so, the visibility queries are executed. The 2 minutes constraint is present
# to avoid executing the visibility queries too frequently
def visibility_2_fun():
    
    global visibility_start_time
    visibility_end_time = time.time()
    visibility_execution_time = visibility_end_time - visibility_start_time
    
    if visibility_execution_time > 300: # 300 seconds = 5 minutes
        print("ERROR: more than 5 minutes elapsed between visibility queries's executions")
        
    elif visibility_execution_time < 300 and visibility_execution_time > 120:
        spark.sql(os.getcwd() + "/ddl/tpcdi_visibility_2.sql")
        visibility_start_time = time.time()
        return
        
    else:
        return

In [9]:
# This function loads audit data into the audit table. It can be used for all the three batches.

def audit_upload(batch_n):
    # Go to Batch1 and consider only the files that end for "audit.csv"
    audit_files = glob.glob(os.getcwd() + "/data/SF"+str(SF) +"/Batch"+ str(batch_n) +"/*_audit.csv")
    
    # For each audit_file...
    sch_audit = spark.sql("select * from audit").schema
    for file_path in audit_files:
        # Place "audit_file" data into a Spark DF
        audit_df = spark.read.schema(sch_audit).csv(file_path, header=True, inferSchema=True)

        # Append data to the Audit table
        audit_df.write.insertInto("Audit", overwrite=False)

In [10]:
# Just before starting the Historical Load: execute the batch validation query
"""
f = open(os.getcwd() + "/ddl/tpcdi_validation.sql", "r")
tables=f.read()
tables = tables.split(";")[:-1]
for i in tables:
    spark.sql(i)"""

#spark.sql(os.getcwd() + "/data/output/tpcdi_validation.sql")

'\nf = open(os.getcwd() + "/ddl/tpcdi_validation.sql", "r")\ntables=f.read()\ntables = tables.split(";")[:-1]\nfor i in tables:\n    spark.sql(i)'

In [ ]:
# Record the end time
end_time_prepa = time.time()
preparation_time = end_time_prepa - start_time_prepa

# Historical Load

In [ ]:
# Record the start time for historical load
start_time_historical = time.time()

In [13]:
#Not_modified_table
for i in Not_modified_table:
    name_file = glob.glob(os.getcwd() + "/data/SF"+str(SF) +"/Batch1/"+ i[0] +".txt")
    df_schema = spark.sql("select * from " + i[1])
    df = spark.read.schema(df_schema.schema).option("delimiter", "|").csv(name_file)
    df.write.mode("overwrite").insertInto(i[1])
            

23/12/24 15:02:02 WARN HiveConf: HiveConf of name hive.stats.jdbc.timeout does not exist
23/12/24 15:02:02 WARN HiveConf: HiveConf of name hive.stats.retries.wait does not exist
23/12/24 15:02:02 ERROR Schema: Failed initialising database.
Unable to open a test connection to the given database. JDBC url = jdbc:derby:;databaseName=metastore_db;create=true, username = APP. Terminating connection pool (set lazyInit to true if you expect to start your database after your app). Original Exception: ------
java.sql.SQLException: Failed to start database 'metastore_db' with class loader sun.misc.Launcher$AppClassLoader@4dd8dc3, see the next exception for details.
	at org.apache.derby.impl.jdbc.SQLExceptionFactory.getSQLException(Unknown Source)
	at org.apache.derby.impl.jdbc.SQLExceptionFactory.getSQLException(Unknown Source)
	at org.apache.derby.impl.jdbc.Util.seeNextException(Unknown Source)
	at org.apache.derby.impl.jdbc.EmbedConnection.bootDatabase(Unknown Source)
	at org.apache.derby.impl

AnalysisException: org.apache.hadoop.hive.ql.metadata.HiveException: java.lang.RuntimeException: Unable to instantiate org.apache.hadoop.hive.ql.metadata.SessionHiveMetaStoreClient

In [ ]:
def string_to_date(string):
    return string[0:4]+"-"+string[4:6]+"-"+string[6:8]
    
def string_to_timestamp(string):
    return string[0:4]+"-"+string[4:6]+"-"+string[6:8]+" " +string[9:11]+":"+string[11:13]+":"+string[13:15]

In [ ]:
#finwire_files = [ finwire_source_files_path + '/' + file for file in os.listdir( finwire_source_files_path ) if re.search( r'^FINWIRE......$', file ) ] 
finwire_combined_df = pd.DataFrame()
finwire_files = glob.glob(os.getcwd() + "/data/SF"+str(SF) +"/Batch1/FINWIRE??????")
finwire_files.sort()

#raise Exception("job done")
start_time_finwire = time.time()
for file_path in finwire_files:

    #Read the file and add to a combined Dataframe
    c_names = ["Content"]
    finwire_df = pd.read_csv(file_path, names=c_names,index_col=False)
    finwire_df['Type'] = pd.DataFrame(finwire_df["Content"].str.slice(15, 18))
    finwire_combined_df = pd.concat([finwire_combined_df, finwire_df], ignore_index=True)
    finwire_df_CMP=finwire_combined_df[finwire_combined_df["Type"]=='CMP']
    finwire_df_FIN=finwire_combined_df[finwire_combined_df["Type"]=='FIN']
    finwire_df_SEC=finwire_combined_df[finwire_combined_df["Type"]=='SEC']
    finwire_df_CMP=pd.DataFrame(finwire_df_CMP[["Content"]])
    finwire_df_FIN=pd.DataFrame(finwire_df_FIN[["Content"]])
    finwire_df_SEC=pd.DataFrame(finwire_df_SEC[["Content"]])
    
    skiprows = 1
    serrogate_key_CMP = 0
    serrogate_key_SEC = 0
    time_flag = 0
    
    
    if finwire_df_CMP.empty  == False:
        finwire_df_CMP.to_csv("CMP", index=False)
        df_CMP = pd.read_fwf("CMP" , colspecs=cmp_colspecs, header = None, skiprows=skiprows)
        
        #some variables
        final_df = []
        sch = spark.sql("select * from DimCompany").schema
        #main boucle
        for index, row in df_CMP.iterrows():
            stop_time_finwire = time.time()
            if stop_time_finwire - start_time_finwire > 60:
                time_flag = 1
            #set value
            Industry = spark.sql("select IN_NAME from INDUSTRY where IN_ID = '" + row[5] + "'").collect()[0][0]
            Status = spark.sql("select ST_NAME from StatusType where ST_ID = '" + row[4] + "'").collect()[0][0]
            # Dimessages
            if row[6] not in valid_ratings:
                df = [(current_timestamp(),1,"DimCompany","Invalid SPRating","Alert",f"CO_ID = {row[3]}, CO_SP_RATE ={row[6]}")]
                #df.write.mode("append").insertInto("DImessages")
                isLowGrade = None
                row[6] = None
                
            else:                
                if row[6].startswith('A') or row[6].startswith('BBB'):
                    isLowGrade = False
                else:
                    isLowGrade = True
            
            if not pd.isna(row[7]):
                row7 = datetime.strptime(str(int(row[7])), '%Y%m%d')
            else:
                row7 = datetime.strptime('0001-01-01', '%Y-%m-%d')
            #reorder
            working_df = [Decimal(serrogate_key_CMP),Decimal(row[3]),Status,row[2],Industry,row[6],isLowGrade,
                          row[14],row[8],row[9],row[10],row[11],row[12],row[13],row[15],
                          row7,True,Decimal(1)
                          ,datetime.strptime(string_to_timestamp(row[0]),'%Y-%m-%d %H:%M:%S'),
                          datetime.strptime('9999-12-31', '%Y-%m-%d')]
            final_df.append(tuple(working_df))
            serrogate_key_CMP += 1
            
        df = spark.createDataFrame(data=final_df,schema=sch)
        df.write.mode("append").insertInto("DimCompany")

    if time_flag == 1:
        break

    if finwire_df_SEC.empty == False:
        finwire_df_SEC.to_csv("SEC", index=False)
        df_SEC = pd.read_fwf("SEC" , colspecs=sec_colspecs, header = None, skiprows=skiprows)
        
        #some variables
        final_df = []
        sch = spark.sql("select * from DimSecurity").schema
        for index, row in df_SEC.iterrows():
            #set value
            SK_SECURITYID = spark.sql("""select SK_CompanyID from DimCompany
                        where (Name == '"""+ str(row[11]) +"""' or CompanyID== '""" 
                      + str(row[11]) + """' ) and EffectiveDate <= '""" + string_to_timestamp(row[0]) +
                      """' and '"""+ string_to_timestamp(row[0]) + """' < EndDate""").collect()[0][0]
            Status = spark.sql("select ST_NAME from StatusType where ST_ID = '" + row[4] + "'").collect()[0][0]
            
            if not pd.isna(row[8]):
                row8 = datetime.strptime(str(int(row[8])), '%Y%m%d')
            else:
                row8 = datetime.strptime('0001-01-01', '%Y-%m-%d')
                
            if not pd.isna(row[9]):
                row9 = datetime.strptime(str(int(row[9])), '%Y%m%d')
            else:
                row9 = datetime.strptime('0001-01-01', '%Y-%m-%d')
            
            
            #reorder
            working_df = [Decimal(serrogate_key_SEC), row[2], row[3], Status, row[5], row[6], 
                          Decimal(SK_SECURITYID), Decimal(row[7]), row8
                         , row9, Decimal(row[10]),True,Decimal(1)
                          ,datetime.strptime(string_to_timestamp(row[0]),'%Y-%m-%d %H:%M:%S'),
                          datetime.strptime('9999-12-31', '%Y-%m-%d')]
            serrogate_key_SEC += 1
            final_df.append(tuple(working_df))
            
        df = spark.createDataFrame(data=final_df,schema=sch)
        df.write.mode("append").insertInto("DimSecurity")
        
        
    if finwire_df_FIN.empty == False:
        finwire_df_FIN.to_csv("FIN", index=False)
        df_FIN = pd.read_fwf("FIN" , colspecs=fin_colspecs, header = None, skiprows=skiprows)
        
        #some variables
        final_df = []
        sch = spark.sql("select * from Financial").schema
        for index, row in df_FIN.iterrows():
            SK_COMPANYID =spark.sql("""select SK_CompanyID from DimCompany
                        where (Name == '"""+ str(row[16]) +"""' or CompanyID== '""" 
                      + str(row[16]) + """' ) and EffectiveDate <= '""" + string_to_timestamp(row[0]) +
                      """' and '"""+ string_to_timestamp(row[0]) + """' < EndDate""").collect()[0][0]
                    
            working_df = [Decimal(SK_COMPANYID), Decimal(row[2]), Decimal(row[3]),
                          datetime.strptime(str(int(row[4])), '%Y%m%d')
                          , Decimal(row[6]), Decimal(row[7]), Decimal(row[8]), Decimal(row[9])
                         , Decimal(row[10]), Decimal(row[11]), Decimal(row[12]), Decimal(row[13])
                          , Decimal(row[14]), Decimal(row[15])]
            final_df.append(tuple(working_df))
            
        df = spark.createDataFrame(data=final_df,schema=sch)
        df.write.mode("append").insertInto("Financial")

In [ ]:
tree = ET.parse(os.getcwd() + "/data/SF"+str(SF) +"/Batch1/CustomerMgmt.xml")
root = tree.getroot()

def finder(obj_name):
    try:
        return Customer.find(f".//{obj_name}").text
    except:
        return ""

# Create the .csv
with open(os.getcwd() + "/data/SF"+str(SF) +"/Batch1/CustomerMgmt.csv", 'w', newline='') as csv_file:
    csv_writer = csv.writer(csv_file)

    # Write the header
    header = row = ['ActionType','ActionTS','C_ID', 'C_TAX_ID', 'C_GNDR', 'C_TIER', 'C_DOB', 'C_L_NAME', 'C_F_NAME', 'C_M_NAME', 'C_ADLINE1', 'C_ADLINE2', 'C_ZIPCODE', 'C_CITY', 'C_STATE_PROV', 'C_CTRY', 'C_PRIM_EMAIL', 'C_ALT_EMAIL', 'C_CTRY_CODE_1', 'C_AREA_CODE_1', 'C_LOCAL_1', 'C_EXT_1', 'C_CTRY_CODE_2', 'C_AREA_CODE_2', 'C_LOCAL_2', 'C_EXT_2', 'C_CTRY_CODE_3', 'C_AREA_CODE_3', 'C_LOCAL_3', 'C_EXT_3', 'C_LCL_TX_ID', 'C_NAT_TX_ID', 'CA_ID', 'CA_TAX_ST', 'CA_B_ID', 'CA_NAME']

    #csv_writer.writerow(header)
    
    # Iteratively add the customers
    for TPCDAction in root:
        row = []

        action_type = TPCDAction.attrib.get("ActionType")
        action_ts = TPCDAction.attrib.get("ActionTS")

        for Customer in TPCDAction:
            c_id = Customer.attrib.get("C_ID")
            c_tax_id = Customer.attrib.get("C_TAX_ID")
            c_gndr = Customer.attrib.get("C_GNDR")
            c_tier = Customer.attrib.get("C_TIER")
            c_dob = Customer.attrib.get("C_DOB")
            
            c_l_name = finder("C_L_NAME")
            c_f_name = finder("C_F_NAME")
            c_m_name = finder("C_M_NAME")
            
            c_adline1 = finder("C_ADLINE1")
            c_adline2 = finder("C_ADLINE2")
            c_zipcode = finder("C_ZIPCODE")
            c_city = finder("C_CITY")
            c_state_prov = finder("C_STATE_PROV")
            c_ctry = finder("C_CTRY")
        
            c_prim_email = finder("C_PRIM_EMAIL")
            c_alt_email = finder("C_ALT_EMAIL")
            
            c_ctry_code_1 = finder("C_PHONE_1//C_CTRY_CODE")
            c_area_code_1 = finder("C_PHONE_1//C_AREA_CODE")
            c_local_1 = finder("C_PHONE_1//C_LOCAL")
            c_ext_1 = finder("C_PHONE_1//C_EXT")
        
            c_ctry_code_2 = finder("C_PHONE_2//C_CTRY_CODE")
            c_area_code_2 = finder("C_PHONE_2//C_AREA_CODE")
            c_local_2 = finder("C_PHONE_2//C_LOCAL")
            c_ext_2 = finder("C_PHONE_2//C_EXT")

            c_ctry_code_3 = finder("C_PHONE_3//C_CTRY_CODE")
            c_area_code_3 = finder("C_PHONE_3//C_AREA_CODE")
            c_local_3 = finder("C_PHONE_3//C_LOCAL")
            c_ext_3 = finder("C_PHONE_3//C_EXT")
            
            c_lcl_tx_id = finder(f"C_LCL_TX_ID")
            c_nat_tx_id = finder(f"C_NAT_TX_ID")
            
            try:
                ca_id = Customer.find(".//Account").attrib.get("CA_ID")
            except:
                ca_id = ""
            
            try:
                ca_tax_st = Customer.find(".//Account").attrib.get("CA_TAX_ST")
            except:
                ca_tax_st = ""
            
            ca_b_id = finder(f"CA_B_ID")
            ca_name = finder(f"CA_NAME")
        
        row = [action_type, action_ts, c_id, c_tax_id, c_gndr, c_tier, c_dob, c_l_name, c_f_name, c_m_name, c_adline1, c_adline2, c_zipcode, c_city, c_state_prov, c_ctry, c_prim_email, c_alt_email, c_ctry_code_1, c_area_code_1, c_local_1, c_ext_1, c_ctry_code_2, c_area_code_2, c_local_2, c_ext_2, c_ctry_code_3, c_area_code_3, c_local_3, c_ext_3, c_lcl_tx_id, c_nat_tx_id, ca_id, ca_tax_st, ca_b_id, ca_name]
        
        csv_writer.writerow(row)   

In [ ]:
from pyspark.sql.functions import col, when, lit, trunc, upper, concat
#Modified_table
for i in Modified_DimTable:
    name_file = glob.glob(os.getcwd() + "/data/SF"+str(SF) +"/Batch1/" +i[0])
    sch = spark.sql("select * from " + i[1]).schema
    if i[0] == "HR.csv":
        print("start DimBroker")
        start_time_HR = time.time()
        time_flag = 0 
        hr_df = pd.read_csv(name_file[0], header=None,sep=r'[,|]')
        broker_df = hr_df[hr_df[5]== 314] # Filter for brokers only
        
        SK_BrokerID = 0
        min_date = spark.sql("select min(DATEVALUE) from DimDate where DATEVALUE <> 'NULL'").collect()[0][0]# Get the earliest date in the DimDate table
        min_date = "0001-01-01 00:00:00"
        final_df = []
        for index, row in broker_df[0:100].iterrows():
            print("HR",index)
            stop_time_HR = time.time()
            if stop_time_HR - start_time_HR > 60:
                time_flag = 1
            if time_flag == 1:
                break
            if pd.isna(row[4]):
                row4=''
            else:
                row4= row[4]
            working_df = [Decimal(SK_BrokerID),Decimal(row[0]),Decimal(row[1])
                          ,row[2],row[3],row4,Decimal(row[5]),row[6],row[7],
                         True,Decimal(1), 
                          datetime.strptime(min_date, '%Y-%m-%d %H:%M:%S'),
                          datetime.strptime("9999-12-31", '%Y-%m-%d')]
            SK_BrokerID +=1
            final_df.append(tuple(working_df))
        df = spark.createDataFrame(data=final_df,schema=sch)
        df.write.mode("overwrite").insertInto(i[1])
        print("Done DimBroker")
                
    elif i[1] == "DimCustomer":
        print("start DimCustomer")
        start_time_Customer = time.time()
        time_flag = 0
        df = pd.read_csv(os.getcwd() + "/data/SF"+str(SF) +"/Batch1/CustomerMgmt.csv", header=None,sep=r'[,|]')
        serrogate_key_Customer = 0
        
        
        sch = spark.sql("select * from " + i[1]).schema
        for index, row in df[0:100].iterrows():
            print("Customer",index)
            stop_time_Customer = time.time()
            if stop_time_Customer - start_time_Customer > 60:
                time_flag = 1
            if time_flag == 1:
                break
            if row[4] == 'F' or  row[4] == 'H':
                Gender = row[4]
            else: 
                Gender ='U'
            Phone1 = str(row[18])+str(row[19])+str(row[20])+str(row[21])
            Phone2 = str(row[22])+str(row[23])+str(row[24])+str(row[25])
            Phone3 = str(row[26])+str(row[27])+str(row[28])+str(row[29])

            NationalTax = spark.sql("select TX_NAME, TX_RATE from TaxRate where TX_ID ='" +str(row[31]) + "'")
            if not NationalTax.isEmpty():
                NationalTaxRateDesc = NationalTax.collect()[0][0]
                NationalTaxRate = NationalTax.collect()[0][1]
            else:
                NationalTaxRateDesc = ''
                NationalTaxRate = 0
            LocalTax = spark.sql("select TX_NAME, TX_RATE from TaxRate where TX_ID = '" + str(row[30]) + "'")
            if not LocalTax.isEmpty():
                LocalTaxRateDesc = LocalTax.collect()[0][0]
                LocalTaxRate = LocalTax.collect()[0][1]
            else:
                LocalTaxRateDesc = ''
                LocalTaxRate = 0
            if not pd.isna(row[6]):
                row6 = datetime.strptime(str(row[6]), '%Y-%m-%d')
            else:
                row6 = datetime.strptime('0001-01-01', '%Y-%m-%d')

            
            working_df = [Decimal(serrogate_key_Customer), Decimal(row[2]),row[3],'ACTIVE', 
                          row[7],row[8],row[9],Gender,Decimal(row[5]),row6,
                         row[10],row[11],row[12],row[13],row[14],row[15],Phone1,Phone2,Phone3,row[16],row[17]
                     ,NationalTaxRateDesc,Decimal(NationalTaxRate),LocalTaxRateDesc,Decimal(LocalTaxRate),
                      '',Decimal(0.0),Decimal(0.0),'',True,
                          Decimal(1),datetime.strptime(row[1].split('T')[0], '%Y-%m-%d'),
                          datetime.strptime('9999-12-31','%Y-%m-%d')]
            for k in np.arange(len(working_df)):
                if type(working_df[k]) == str:
                    working_df[k]= working_df[k].replace('nan', '')
                if pd.isna(working_df[k]) and type(working_df[k]) != type(Decimal(0)):
                    working_df[k]=''
            if row[0] == 'NEW':
                df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
                df.write.mode("append").insertInto(i[1])
                
            elif row[0] == 'UPDCUST' or row[0] == 'INACT':
                
                tm=spark.sql("select * from DimCustomer where CUSTOMERID == '"+str(row[2])+"'")
                if row[6] == '':
                    working_df[9] = tm.collect()[0][9]
                
                print(len(working_df))
                for j in range(len(working_df)):
                    print(j)
                    if working_df[j] == '':
                        working_df[j] = tm.collect()[0][j]
                if row[0] == 'INACT':
                    working_df[3] = 'INACTIVE'
                
                
                df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
                df.write.mode("append").insertInto(i[1])     
            serrogate_key_Customer+=1
        print("Done DimCustomer")
            
            # DImessages
            #if row[5] not in [1,2,3]:
             #   df = [(current_timestamp(),1,"DimCustomer","Invalid customer tier","Alert",f"C_ID = {row[2]}, C_TIER ={row[5]}")]
                #df.write.mode("append").insertInto("DImessages")
                
            #if row[6] < '1923-11-15' or row[6] > '2023-11-15':
                #df = [(current_timestamp(),1,"DimCustomer","DOB out of range","Alert",f"C_ID = {row[2]}, C_DOB ={row[6]}")]
                #df.write.mode("append").insertInto("DImessages")
            # ---
        
                 
                                        
                                        
    elif i[1] == "DimAccount":
        print("start DimAccount")
        start_time_Account = time.time()
        time_flag = 0
        df = pd.read_csv(os.getcwd() + "/data/SF"+str(SF) +"/Batch1/CustomerMgmt.csv", header=None,sep=r'[,|]')

        sch = spark.sql("select * from " + i[1]).schema
        serrogate_key_Account = 0
        for index, row in df[0:100].iterrows():
            print("Account",index)
            stop_time_Account = time.time()
            if stop_time_Account - start_time_Account > 60:
                time_flag = 1
            if time_flag == 1:
                break
            action_type = row[0]
            effective_date = row[1].replace("T", " ")
            
            # Filter DimCustomer to get the relevant CustomerID based on C_ID and effective date
            SK_CustomerID = spark.sql("select SK_CustomerID from DimCustomer where EffectiveDate <= '"+ effective_date 
                                        +"' and EndDate >= '"+ effective_date 
                                        +"' and CustomerID == '" + str(row[2]) + "'").collect()[0][0]
            if not pd.isna(row[34]):
            # Filter DimBroker to get the relevant BrokerID based on CA_B_ID and effective date
                SK_BrokerID = spark.sql("select SK_BrokerID from DimBroker where EffectiveDate <= '"+ effective_date 
                                            +"' and EndDate >= '"+ effective_date 
                                            +"' and BrokerID == '" + str(int(row[34])) + "'")
            else:
                SK_BrokerID = row[34]
            
            if action_type in ['NEW', 'ADDACCT']:
                if SK_BrokerID.isEmpty:
                    SK_BrokerID = -1
                else:
                    SK_BrokerID = SK_BrokerID.collect()[0][0]
                    
                working_df = [Decimal(serrogate_key_Account), Decimal(row[32]), Decimal(SK_BrokerID), Decimal(SK_CustomerID), 'ACTIVE', row[35],
                                      Decimal(row[33]), True, Decimal(1), datetime.strptime(effective_date, '%Y-%m-%d %H:%M:%S'), 
                              datetime.strptime('9999-12-31','%Y-%m-%d')]
                
                for k in range(len(working_df)):
                    if type(working_df[k]) == str:
                        working_df[k]= working_df[k].replace('nan', '')
                    if pd.isna(working_df[k]) and type(working_df[k]) != type(Decimal(0)):
                        working_df[k]=''
                df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
                df.write.mode("append").insertInto(i[1])

                
            elif action_type == 'UPDACCT':
                
                tmp_df = spark.sql("select * from DimAccount where AccountID =='" + str(row[32])+"'")
                if type(SK_BrokerID) not in (int, float, str):
                    if SK_BrokerID.isEmpty:
                        SK_BrokerID = Decimal(-1)
                    else:
                        SK_BrokerID = SK_BrokerID.collect()[0][0]

                working_df =[Decimal(serrogate_key_Account), Decimal(row[32]),SK_BrokerID,
                             Decimal(SK_CustomerID), 'ACTIVE', row[35],
                                      Decimal(row[33]), True, Decimal(1), datetime.strptime(effective_date, '%Y-%m-%d %H:%M:%S'), 
                              datetime.strptime('9999-12-31','%Y-%m-%d')]
                for k in range(len(working_df)):
                    if pd.isna(working_df[k]):
                        working_df[k] = tmp_df.collect()[0][k]
                        
                df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
                df.write.mode("append").insertInto(i[1])
                        
            elif action_type == 'CLOSEACCT':
                tmp_df = spark.sql("select * from DimAccount where AccountID =='" + str(row[32])+"'")
                
                for k in range(len(working_df)):
                    if k == 0:
                        working_df[k] =Decimal(serrogate_key_Account)
                    elif k == 4:
                        working_df[k] ='INACTIVE'
                    elif k == 7:
                        working_df[k] =False    
                    else:
                        working_df[k] =tmp_df.collect()[0][k]
                df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
                df.write.mode("append").insertInto(i[1])
            elif action_type in ['UPDCUST','INACT']:
                pass
                        
            serrogate_key_Account += 1
        print("Done DimAccount")
        
    
        
    elif i[1] == "DimTrade0":
        print("start DimTrade")
        start_time_Trade = time.time()
        time_flag = 0
        trade_data = pd.read_csv(os.getcwd() + "/data/SF"+str(SF) +"/Batch1/Trade.txt", sep='|', header=None)
        trade_history_data = pd.read_csv(os.getcwd() + "/data/SF"+str(SF) +"/Batch1/TradeHistory.txt", sep='|', header=None)
        
        sch = spark.sql("select * from " + i[1]).schema
        for index, row in trade_data[0:100].iterrows():
            print("Trade",index)
            stop_time_Trade = time.time()
            if stop_time_Trade - start_time_Trade > 60:
                time_flag = 1
            if time_flag == 1:
                break
            time_sql = spark.sql("select SK_TIMEID from DimTime where SECONDDESC == '"+row[1].split(" ")[1] + "'").collect()[0][0]
            date = spark.sql("select SK_DATEID from DimDate where DATEVALUE == '"+row[1].split(" ")[0] + "'").collect()[0][0]
            
            
            if (row[2] == "SBMT" and (row[3] == "TMB" or row[3] == "TMS")) or row[2] == "PNDG":
                SK_CreateDateID = date
                SK_CreateTimeID = time_sql
                SK_CloseDateID = Decimal('nan')
                SK_CloseTimeID = Decimal('nan')

            elif row[2] in ['CMPT', 'CNCL']:
                print(row[1])
                SK_CreateDateID = Decimal('nan')
                SK_CreateTimeID = Decimal('nan')
                SK_CloseDateID = date
                SK_CloseTimeID = time_sql
            
            tmp = 0
            SK_BrokerID = tmp#.collect()[0][0]
            SK_CustomerID = tmp#.collect()[0][1]
            SK_AccountID = tmp#.collect()[0][2]
            Status = spark.sql("select ST_NAME from StatusType where ST_ID = '" + row[2]+ "'" )
            Type = spark.sql("select TT_NAME from TradeType where TT_ID = '" + row[3]+ "'" )
            
            if type(row[0]) == str:
                tmp = spark.sql("select SK_SecurityID, SK_CompanyID from DimSecurity where SYMBOL = '" + row[1] + 
                                             "' and EFFECTIVEDATE ="+row[0] +"'")
                SK_SecurityID = tmp.collect()[0][0]
                SK_CompanyID = tmp.collect()[0][1]
            else:
                SK_SecurityID = 0
                SK_CompanyID = 0
            if row[4] == 0:
                row[4] = False
            else:
                row[4] = True

            working_df = [Decimal(1), Decimal(SK_BrokerID), Decimal(SK_CreateDateID), 
                          Decimal(SK_CreateTimeID), Decimal(SK_CloseDateID),Decimal(SK_CloseTimeID)
                          , Status, Type, row[4], Decimal(SK_SecurityID),Decimal(SK_CompanyID),
                            Decimal(row[6]), Decimal(row[7]), Decimal(SK_CustomerID), Decimal(SK_AccountID)
                          , row[9], Decimal(row[10]), Decimal(row[11]),
                                          Decimal(row[12]), Decimal(row[13]), Decimal(1)]
            df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
            df.write.mode("append").insertInto(i[1])
        print("Done DimTrade")
            
            # DImessages
            #if row[17] is not None and row[17] > (row[16] * row[11]):
             #   df = [(current_timestamp(),Decimal(1),"DimTrade","Invalid trade fee","Alert",f"T_ID = {row[0]}, T_CHRG ={row[17]}")]
                #df.write.mode("append").insertInto("DImessages")
                
            #if row[18] is not None and row[18] > (row[16] * row[11]):
             #   df = [(current_timestamp(),Decimal(1),"DimTrade","Invalid trade commission","Alert",f"T_ID = {row[0]}, T_COMM ={row[18]}")]
                #df.write.mode("append").insertInto("DImessages")
            # ---

start DimCustomer
Customer 0


/tmp/ipykernel_6156/1262976459.py:43: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  df = pd.read_csv(os.getcwd() + "/data/SF"+str(SF) +"/Batch1/CustomerMgmt.csv", header=None,sep=r'[,|]')


Customer 1
Customer 2
Customer 3
Customer 4
Customer 5
Customer 6
Customer 7
Customer 8
Customer 9
Customer 10
Customer 11
Customer 12
Customer 13
Customer 14
Customer 15
Customer 16
Customer 17
Customer 18
Customer 19
Customer 20
Customer 21
Customer 22
Customer 23
Customer 24
Customer 25
33
0
1
2


3
4


5


...

Account 5


Account 6


Account 7


Account 8


Account 9
Done DimAccount


In [ ]:
for i in Modified_FactTable:
    name_file = glob.glob(os.getcwd() + "/data/SF"+str(SF) +"/Batch1/" +i[0])
    if True:
        df = pd.read_csv(name_file[0], header=None,sep=r'[,|]')
        final_df = []
        sch = spark.sql("select * from " + i[1]).schema
        for index, row in df[0:100].iterrows():
            working_df = []

            if i[1] == "FactCashBalances":
                print("FactCashBalances")
                start_time_CashBalances = time.time()
                time_flag = 0
                #set value
                info_dim=spark.sql(f"""SELECT SK_CustomerID,SK_AccountID FROM DimAccount
                                        WHERE ACCOUNTID = {row[0]} AND EFFECTIVEDATE <= '{row[1].split(" ")[0]}'
                                        AND '{row[1].split(" ")[0]}' <= ENDDATE""")

                SK_CustomerID=info_dim.collect()[0][0]
                SK_AccountID=info_dim.collect()[0][1]
                SK_DateID = spark.sql(f"""SELECT SK_DateID FROM DimDate
                                        where DateValue = '{row[1].split(" ")[0]}' """).collect()[0][0]
                Cash =  spark.sql("select SK_DateID from DimDate where DateValue = '" + row[1] + "'").collect()[0][0]
                BatchID =1
                working_df = [Decimal(SK_CustomerID),Decimal(SK_AccountID),Decimal(SK_DateID),Decimal(Cash),
                              Decimal(BatchID)]
            
                df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
                df.write.mode("append").insertInto(i[1])
                print("Done FactCashBalances")
                
            
            elif i[1] == "FactMarketHistory":
                print("FactMarketHistory")
                #set value
                tmp = spark.sql("SELECT SK_SecurityID, SK_CompanyID FROM DimSecurity WHERE IsCurrent = 1")
                SK_SECURITYID = tmp.collect()[0][0]
                SK_COMPANYID = tmp.collect()[0][1]
                SK_DATEID= spark.sql("select SK_DATEID from DimDate where DateValue = '" + row[0] + "'").select("SK_DATEID").collect()[0][0]
                PERATIO= 0 
                #YIELD= spark.sql("select dividend from DimSecurity where SYMBOL = '" + row[1] + "'and "+row[0]+" between EffectiveDate and EndDate").collect()[0][0]
                YIELD = 0 
                
                FIFTYTWOWEEKHIGH = 0 #spark.sql("select max(DM_HIGH) from FactMarketHistory where '" + row[0] +"' <> date_sub("+row[0]+", 365)")
                FIFTYTWOWEEKLOW= 0 #spark.sql("select min(DM_LOW) from FactMarketHistory where '" + row[0] +"' <> date_sub("+row[0]+", 365)")
                SK_FIFTYTWOWEEKLOWDATE = 0
                SK_FIFTYTWOWEEKHIGHDATE = 0                                                        #         " from tmp where" + row[0] +" <> date_sub("+row[0]+", 365))"

                CLOSEPRICE=row[2]
                DAYHIGH=row[3]
                DAYLOW=row[4]
                VOLUME=row[5]
                BATCHID=1

                working_df = [Decimal(SK_SECURITYID),Decimal(SK_COMPANYID),
                              Decimal(SK_DATEID),Decimal(PERATIO),Decimal(YIELD),
                              Decimal(FIFTYTWOWEEKHIGH),
                              Decimal(SK_FIFTYTWOWEEKHIGHDATE),
                              Decimal(FIFTYTWOWEEKLOW),Decimal(SK_FIFTYTWOWEEKLOWDATE),
                              Decimal(CLOSEPRICE),Decimal(DAYHIGH),Decimal(DAYLOW),Decimal(VOLUME),Decimal(BATCHID)]
                
                df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
                df.write.mode("append").insertInto(i[1])
                
                # DImessages
                #if row[3] is None:
                 #    df = [(current_timestamp(),1,"FactMarketHistory","No earnings for company","Alert",f"DM_S_SYMB={row[3]}")]
                  #   df.write.mode("append").insertInto("DImessages")
                # ---
                print("Done FactMarketHistory")

            elif i[1] == "FactWatches":
                print("FactWatches")
                if row[3]=="ACTV":
                    SK_CUSTOMERID = spark.sql(f"""
                                        SELECT SK_CUSTOMERID
                                        FROM DimCustomer
                                        WHERE CUSTOMERID = {row[0]} """).collect()[0][0] 
                    if row[1] in spark.sql("SELECT SK_SecurityID FROM DimSecurity").collect():
                        SK_SECURITYID = spark.sql(f"""
                                        SELECT SK_SecurityID
                                        FROM DimSecurity
                                        WHERE SYMBOL = '{row[1]}' """).collect()[0][0]
                    else:
                        SK_SECURITYID = Decimal(0)
                    SK_DATEID_DATEPLACED= int(row[2].split(' ')[0].replace('-', ''))
                    SK_DATEID_DATEREMOVED = 'nan'
                    BATCHID=1

                    working_df = [SK_CUSTOMERID,SK_SECURITYID,
                    Decimal(SK_DATEID_DATEPLACED),
                    Decimal(SK_DATEID_DATEREMOVED),
                    Decimal(BATCHID)]

                    df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
                    df.write.mode("append").insertInto(i[1])
                if row[3]=="CNCL":
                    pass # no delete possible
                print("Done FactWatches")


            elif i[1] == "FactHoldings": 
                print("FactHoldings")
                TRADEID = int(row[0])
                CURRENTTRADEID = int(row[1])
                df = ''#spark.sql("""select SK_CustomerID,SK_AccountID,SK_SecurityID,SK_CompanyID,
                #SK_CloseDateID,SK_CloseTimeID, SK_AccountID
                 #              from DimTrade where TradeID = '""" + str(row[1]) + "'")
                
                SK_CUSTOMERID = 0#df.collect()[0][0]
                SK_ACCOUNTID = 0#df.collect()[0][1]
                SK_SECURITYID = 0#df.collect()[0][2]
                SK_COMPANYID = 0#df.collect()[0][3]
                SK_DATEID =0#df.collect()[0][4]
                SK_TIMEID = 0#df.collect()[0][5]
                CURRENTPRICE =0#df.collect()[0][6]
                CURRENTHOLDING = int(row[3])
                BATCHID = 1                                                            
                working_df = [Decimal(TRADEID),Decimal(CURRENTTRADEID),Decimal(SK_CUSTOMERID),
                Decimal(SK_ACCOUNTID),Decimal(SK_SECURITYID),Decimal(SK_COMPANYID),
                Decimal(SK_DATEID),Decimal(SK_TIMEID),
                Decimal(CURRENTPRICE),Decimal(CURRENTHOLDING),Decimal(BATCHID)]
                
                df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
                df.write.mode("append").insertInto(i[1])
                print("Done FactHoldings")
            elif i[1] == "Prospect":
                print("Prospect")
                isCustomer = spark.sql("select * from DimCustomer where status = 'ACTIVE' ")#to-do
                if isCustomer.count() == 0:
                    isCustomer = False
                else:
                    isCustomer = True
                SK_RecordDateID = 0 
                SK_UpdateDateID = 0 
                
                MarketingNameplate = ""
                if row[12] > 200000 or row[21] > 1000000:
                    MarketingNameplate += "+HighValue"
                if row[14] > 3 or row[20] > 5:
                    MarketingNameplate += "+Expenses"
                if row[16] > 45:
                    MarketingNameplate += "+Boomer"
                if row[12] < 100000 or row[21] < 50000 or row[17] < 600:
                    MarketingNameplate += "+MoneyAlert"
                if row[13] > 3 or row[20] > 7 :
                    MarketingNameplate += "+Spender"
                if row[16] < 25 and row[12] > 1000000 :
                    MarketingNameplate += "+Inherited"
                if len(MarketingNameplate) != 0:
                    MarketingNameplate = MarketingNameplate[1:]
                
                
                working_df = [row[0],Decimal(SK_RecordDateID),
                            Decimal(SK_UpdateDateID),Decimal(1),isCustomer
                            ,row[1],row[2],row[3],row[4],row[5],row[6]
                            ,row[7],row[8],row[9],row[10]
                            ,row[11],Decimal(row[12]),Decimal(row[13]),Decimal(row[14]),
                            row[15],Decimal(row[16]),Decimal(row[17])
                              ,row[18],row[19],Decimal(row[20]),Decimal(row[21]),MarketingNameplate]
                for k in range(len(working_df)):
                    if pd.isna(working_df[k]) and type(working_df[k]) != type(Decimal(0)):
                        working_df[k] = ''
                df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
                df.write.mode("append").insertInto(i[1])
                print("Done Prospect")
        #if i[1] == "Prospect":
            #df = [(current_timestamp(),Decimal(1),"Prospect","Inserted rows","Status",prospect_count)]
            #df.write.mode("append").insertInto("DImessages")


/tmp/ipykernel_6156/479335090.py:4: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  df = pd.read_csv(name_file[0], header=None,sep=r'[,|]')
23/12/24 14:56:42 WARN HiveConf: HiveConf of name hive.internal.ss.authz.settings.applied.marker does not exist
23/12/24 14:56:42 WARN HiveConf: HiveConf of name hive.stats.jdbc.timeout does not exist
23/12/24 14:56:42 WARN HiveConf: HiveConf of name hive.stats.retries.wait does not exist


FactCashBalances
Done FactCashBalances
FactCashBalances


Exception in thread "serve-DataFrame" java.net.SocketTimeoutException: Accept timed out
	at java.net.PlainSocketImpl.socketAccept(Native Method)
	at java.net.AbstractPlainSocketImpl.accept(AbstractPlainSocketImpl.java:409)
	at java.net.ServerSocket.implAccept(ServerSocket.java:560)
	at java.net.ServerSocket.accept(ServerSocket.java:528)
	at org.apache.spark.security.SocketAuthServer$$anon$1.run(SocketAuthServer.scala:65)


Done FactCashBalances
FactCashBalances
Done FactCashBalances
FactCashBalances
Done FactCashBalances
FactCashBalances
Done FactCashBalances
FactCashBalances
Done FactCashBalances
FactCashBalances


Done FactCashBalances
FactCashBalances


...

Done Prospect
Prospect


Done Prospect
Prospect


Done Prospect
Prospect


Done Prospect
Prospect


Done Prospect


In [ ]:
# Execute the following line during the Historical Phase
"""audit_upload(1)

# At the end of the Historical Load: execute the batch validation query
#spark.sql(os.getcwd() + "/data/output/tpcdi_validation.sql")

f = open(os.getcwd() + "/ddl/tpcdi_validation.sql", "r")
tables=f.read()
tables = tables.split(";")[:-1]
for i in tables:
    spark.sql(i)"""

In [ ]:
# Record the end time
end_time_histo = time.time()
time_histo = end_time_histo - start_time_historical

## Incremental Load

In [ ]:
"""# Run Visibility 1 at the start of incremental
#spark.sql(os.getcwd() + "/data/output/tpcdi_visibility_1.sql")

f = open(os.getcwd() + "/ddl/tpcdi_visibility_1.sql", "r")
tables=f.read()
tables = tables.split(";")[:-1]
for i in tables:
    spark.sql(i)

# Run Visibility 2 right after visibility 1
#spark.sql(os.getcwd() + "/data/output/tpcdi_visibility_2.sql")

f = open(os.getcwd() + "/tpcdi_visibility_2.sql", "r")
tables=f.read()
tables = tables.split(";")[:-1]
for i in tables:
    spark.sql(i)

# Register time
start_time = time.time()"""

In [ ]:
def incr_DimAccount(batch_id):
    
    account_data = pd.read_csv(os.getcwd() + "/data/SF"+str(SF) +"/Batch"+str(batch_id) +"/Account.txt", header=None,sep=r'[,|]')
    sch = spark.sql("select * from DimAccount").schema
    account_data.columns = ['I/U', 'CA_ID', 'CA_NAME', 'CA_TAX_ST', 'CA_B_ID', 'CA_C_ID', 'CA_ST_ID', 'CDC_FLAG']
    serrogate_key_Account = spark.sql("select max(SK_ACCOUNTID) from DimAccount").collect()[0][0]
    for index, row in account_data[0:100].iterrows():
        if row[0] == "I":
            pass
        elif row[0] == "U":
            pass
        
        SK_BrokerID = Decimal(0)#spark.sql("select SK_BrokerID from DimBroker where BrokerID == '"+str(row[4])+"'").collect()[0][0]
        SK_CustomerID = Decimal(0) #spark.sql("select SK_CustomerID from DimCustomer where CustomerID == '"+str(row[5])+"'").collect()[0][0]
        
        Status = Decimal(0) #spark.sql("select ST_NAME from StatusType where ST_ID == '"+str(row[6])+"'")
        working_df_account = [Decimal(serrogate_key_Account), Decimal(row[1]), Decimal(SK_BrokerID), 
                              Decimal(SK_CustomerID), Status, row[2], Decimal(row[3]), True, 
                              Decimal(batch_id), datetime.strptime('9999-01-01', '%Y-%m-%d'), 
                              datetime.strptime('9999-12-31','%Y-%m-%d')]
        for k in range(len(working_df_account)):
            if type(working_df_account[k]) == str:
                working_df_account[k]= working_df_account[k].replace('nan', '')
            if pd.isna(working_df_account[k]) and type(working_df_account[k]) != type(Decimal(0)):
                working_df[k]=''
        df = spark.createDataFrame(data=[tuple(working_df_account)],schema=sch)
        #df.write.mode("append").insertInto("DimAccount")
        
        serrogate_key_Account += 1
    print("Done DimAccount")
        
    
    #sch = spark.sql("select * from DimAccount").schema
    #df = spark.read.schema(sch).csv(os.getcwd() + "/result/Batch" + str(batch_id) + "_DimAccount.csv", sep=',')   
    #df.write.mode("append").insertInto("DimAccount")
    

def incr_DimCustomer(batch_id):

    customer_data = pd.read_csv(os.getcwd() + "/data/SF"+str(SF) +"/Batch"+str(batch_id) +"/Customer.txt", header=None,sep=r'[,|]')
    sch = spark.sql("select * from DimCustomer").schema
    serrogate_key_Customer = spark.sql("select max(SK_CUSTOMERID) from DimCustomer").collect()[0][0]
    for index, row in customer_data[0:100].iterrows():
        if row[0] == "I":
            pass
        elif row[0] == "U":
            pass
        if row[8] == 'F' or  row[8] == 'H':
            Gender = row[8]
        else: 
            Gender ='U'

        #matching_status_record = StatusType[StatusType['ST_ID'] == row[4]]
        #SK_StatusID = matching_status_record['SK_StatusID'].values[0]
        SK_StatusID = Decimal(0)#spark.sql("select SK_StatusID from StatusType where ST_ID == '"+str(row[4])+"'").collect()[0][0]
        Phone1 = str(row[18])+str(row[19])+str(row[20])+str(row[21])
        Phone2 = str(row[22])+str(row[23])+str(row[24])+str(row[25])
        Phone3 = str(row[26])+str(row[27])+str(row[28])+str(row[29])

        NationalTax = spark.sql("select TX_NAME, TX_RATE from TaxRate where TX_ID ='" +str(row[31]) + "'")
        NationalTaxRateDesc = NationalTax.collect()[0][0]
        NationalTaxRate = NationalTax.collect()[0][1]

        #LocalTax = spark.sql("select TX_NAME, TX_RATE from TaxRate where TX_ID = '" + str(row[30]) + "'")
        LocalTaxRateDesc = '' #LocalTax.collect()[0][0]
        LocalTaxRate = 0 #LocalTax.collect()[1][0]

        working_df_customer = [Decimal(serrogate_key_Customer), Decimal(row[2]),row[3],'ACTIVE', 
                          row[7],row[8],row[9],Gender,Decimal(row[9]),row6,
                         row[10],row[11],row[12],row[13],row[14],row[15],Phone1,Phone2,Phone3,row[16],row[17]
                     ,NationalTaxRateDesc,Decimal(NationalTaxRate),LocalTaxRateDesc,Decimal(LocalTaxRate),
                      '',Decimal(0.0),Decimal(0.0),'',True,
                          Decimal(1),datetime.strptime('9999-01-01', '%Y-%m-%d'),
                          datetime.strptime('9999-12-31','%Y-%m-%d')]

        for k in range(len(working_df_customer)):
            if type(working_df_customer[k]) == str:
                working_df_customer[k]= working_df_customer[k].replace('nan', '')
            if pd.isna(working_df_customer[k]) and type(working_df_customer[k]) != type(Decimal(0)):
                working_df_customer[k]=''
        df = spark.createDataFrame(data=[tuple(working_df_customer)],schema=sch)
        #df.write.mode("append").insertInto("DimCustomer")

        #serrogate_key_Customer += 1
        
        # VALERIO DIMESSAGES
        #if row[5] not in [1,2,3]:
         #       df = [(current_timestamp(),batch_id,"DimCustomer","Invalid customer tier","Alert",f"C_ID = {row[2]}, C_TIER ={row[5]}")]
         #       df.write.mode("append").insertInto("DImessages")
                
       # if row[6] < datetime(1923,11,15) or row[6] > (2023,11,15):
        #    df = [(current_timestamp(),batch_id,"DimCustomer","DOB out of range","Alert",f"C_ID = {row[2]}, C_DOB ={row[6]}")]
        #    df.write.mode("append").insertInto("DImessages")
        # ---
    

def inc_FactCashBalance(batch_id):
    print("start FactCashBalance")
    
    cash_transaction_data = pd.read_csv(os.getcwd() + "/data/SF"+str(SF) +"/Batch"+str(batch_id) +"/CashTransaction.txt", header=None,sep=r'[,|]')
    sch = spark.sql("select * from FactCashBalances").schema
    cash_transaction_data.columns = ["CDC_FLAG", "CDC_DSN", "CT_CA_ID", "CT_DTS", "CT_AMT", "CT_NAME"]
    for index, row in cash_transaction_data[0:100].iterrows():
        if row["CDC_FLAG"] == "I":
            pass
        elif row['CDC_FLAG'] == "U":
            pass

        
        tmp = ""#spark.sql("select SK_CustomerID, SK_AccountID from DimAccount where AccountID = '" 
                 #  + row[2] + "' and isCurrent == '1'" )
        SK_CustomerID = 0
        SK_AccountID = 0
        SK_DateID = spark.sql("select SK_DateID from DimDate where DateValue == '"+ row[3]+"'").collect()[0][0]
        Cash = row[4]
        # "Cash is calculated as the sum of the prior Cash amount for this account plus the sum of all CT_AMT values from all transactions in this account on this day. If there is no previous FactCashBalances record for the associated account, zero is used."
        #Cash = spark.sql("select Cash from FactCashBalance where SK_AccountID == '"+ SK_AccountID +"' and SK_DateID == '"+ SK_DateID +"'").collect()[0][0]

        working_df = [Decimal(SK_CustomerID),Decimal(SK_AccountID),Decimal(SK_DateID),Decimal(Cash),
                        Decimal(BatchID)]
    
    df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
    #df.write.mode("append").insertInto("FactCashBalances")
    print("Done FactCashBalances")
        
def inc_DimTrade(batch_id): 
        
    trade_data=  pd.read_csv(os.getcwd() + "/data/SF"+str(SF) +"/Batch"+str(batch_id) +"/Trade.txt", header=None,sep=r'[,|]')
    trade_data.columns = ['CDC_FLAG', 'T_ID', 'T_CA_ID', 'T_DTS', 'T_ST_ID', 'T_TT_ID', 'T_IS_CASH', 'T_S_SYMB', 
                          'T_QTY', 'T_BID_PRICE', 'T_CA_ID_B', 'T_CA_ID_S', 'T_TRADE_PRICE', 'T_CHRG', 'T_COMM', 'T_TAX']
    sch = spark.sql("select * from DimTrade").schema

    for index, row in trade_data[0:100].iterrows():
        SK_CreateDateID = row[3].split(" ")[0]
        SK_CreateTimeID = row[3].split(" ")[1]
        SK_CloseDateID = None
        SK_CloseTimeID = None
        if row[4] in ["CMPT", "CNCL"]:
            SK_CloseDateID = row[3].split(" ")[0]
            SK_CloseTimeID = row[3].split(" ")[1]
        tmp = ""#spark.sql("select SK_AccountID, SK_CustomerID, SK_BrokerID from DimAccount where AccountID = '" 
                 #                       + row[2] + "' and IsCurrent = '1'")
        SK_BrokerID = 0
        SK_CustomerID = 0
        SK_AccountID = 0
        Status = spark.sql("select ST_NAME from StatusType where ST_ID = '" + row[4]+ "'" )
        Type = spark.sql("select TT_NAME from TradeType where TT_ID = '" + row[5]+ "'" )
        tmp = ""#spark.sql("select SK_SecurityID, SK_CompanyID from DimSecurity where SYMBOL = '" + row[7] + 
                 #                    "' and IsCurrent = '1'")
        SK_SecurityID = 0
        SK_CompanyID = 0

        working_df_trade = [Decimal(row[1]), Decimal(SK_BrokerID), datetime.strptime(SK_CreateDateID, '%Y-%m-%d'), 
                            datetime.strptime(SK_CreateTimeID, '%H:%M:%S'), SK_CloseDateID, SK_CloseTimeID, Status, 
                            Type, row[6], Decimal(SK_SecurityID), Decimal(SK_CompanyID),
                            Decimal(row[8]), Decimal(row[9]), Decimal(SK_CustomerID), Decimal(SK_AccountID), row[11], 
                            Decimal(row[12]), Decimal(row[13]), Decimal(row[14]), Decimal(row[15]), Decimal(batch_id)]
        df = spark.createDataFrame(data=[tuple(working_df_trade)],schema=sch)
        #df.write.mode("append").insertInto("DimTrade")
        
        # DImessages
        if row[17] is not None and row[17] > (row[16] * row[11]):
            df = [(current_timestamp(),batch_id,"DimTrade","Invalid trade fee","Alert",f"T_ID = {row[0]}, T_CHRG ={row[17]}")]
            df.write.mode("append").insertInto("DImessages")
                
        if row[18] is not None and row[18] > (row[16] * row[11]):
            df = [(current_timestamp(),batch_id,"DimTrade","Invalid trade commission","Alert",f"T_ID = {row[0]}, T_COMM ={row[18]}")]
            df.write.mode("append").insertInto("DImessages")
        # ---



In [ ]:
def inc_FactHoldings(batch_id): 
    print("start FactHoldings")
        
    data=  pd.read_csv(os.getcwd() + "/data/SF"+str(SF) +"/Batch"+str(batch_id) +"/HoldingHistory.txt", header=None,sep=r'[,|]')
    sch = spark.sql("select * from FactHoldings").schema

    for index, row in data[0:100].iterrows():
        working_df = []
        TRADEID = row[2]
        CURRENTTRADEID = row[3]
        CURRENTHOLDING = row[5]
        
        #df = spark.sql("""select SK_CustomerID,SK_AccountID,SK_SECURITYID,SK_COMPANYID,
         #               SK_CLOSEDATEID,SK_CloseTimeID, SK_AccountID
         #                      from DimTrade where TradeID = '""" + str(row[3]) + "'")
        # if does not work, substitute with zero
        SK_CUSTOMERID = 0#df.collect()[0][0] #0
        SK_ACCOUNTID = 0#df.collect()[0][1] #0
        SK_SECURITYID = 0#df.collect()[0][2] #0
        SK_COMPANYID = 0#df.collect()[0][3] #0
        SK_DATEID = 0#df.collect()[0][4] #0
        SK_TIMEID = 0#df.collect()[0][5] #0
        CURRENTPRICE = 0#df.collect()[0][6] #0

        working_df = [Decimal(TRADEID), Decimal(CURRENTTRADEID), Decimal(SK_CUSTOMERID),
        Decimal(SK_ACCOUNTID), Decimal(SK_SECURITYID), Decimal(SK_COMPANYID),
        Decimal(SK_DATEID), Decimal(SK_TIMEID), Decimal(CURRENTPRICE),
        Decimal(CURRENTHOLDING), Decimal(batch_id)]
        df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
        df.write.mode("append").insertInto("FactHoldings")
    
    
def inc_FactMarketHistory(batch_id): 
        
    data=  pd.read_csv(os.getcwd() + "/data/SF"+str(SF) +"/Batch"+str(batch_id) +"/DailyMarket.txt", header=None,sep=r'[,|]')
    sch = spark.sql("select * from FactMarketHistory").schema

    for index, row in data[0:100].iterrows():
        working_df = []
        tmp = '' #spark.sql("select SK_CustomerID, SK_CompanyID from DimSecurity where Symbol = '" + row[3] + " where IsCurrent = '1'")
        SK_SECURITYID = 0 #tmp.collect()[0][0]
        SK_COMPANYID = 0 #tmp.collect()[0][1]
        SK_DATEID = 0 #spark.sql("select SK_DateID from DimDate where DateValue = '" + row[2] + "'")
        PERATIO = 0
        YIELD = 0 #spark.sql("select dividend from DimSecurity where Symbol = '" + row[3] + " where IsCurrent = '1'")/row[4]*100
        
        
        FIFTYTWOWEEKHIGH = 0#spark.sql("select max(DM_HIGH) from FactMarketHistory 
                        #where" + row[0] +" <> date_sub("+row[0]+", 365))"
        FIFTYTWOWEEKLOW= 0 #spark.sql("select min(DM_LOW) from FactMarketHistory 
                        #where" + row[0] +" <> date_sub("+row[0]+", 365))"
        SK_FIFTYTWOWEEKLOWDATE = 0
        SK_FIFTYTWOWEEKHIGHDATE = 0
        CLOSEPRICE = row[4] 
        DAYHIGH = row[5]
        DAYLOW = row[6]
        VOLUME = row[7]

        working_df = [Decimal(SK_SECURITYID),Decimal(SK_COMPANYID),Decimal(SK_DATEID),
        Decimal(PERATIO),Decimal(YIELD),Decimal(FIFTYTWOWEEKHIGH),
        Decimal(FIFTYTWOWEEKHIGH),Decimal(FIFTYTWOWEEKLOW),
        Decimal(SK_FIFTYTWOWEEKLOWDATE),Decimal(CLOSEPRICE),
        Decimal(DAYHIGH),Decimal(DAYLOW),Decimal(VOLUME),Decimal(batch_id)]
        df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
        df.write.mode("append").insertInto("FactMarketHistory")

        if row[3] is None:
            df = [(current_timestamp(),batch_id,"FactMarketHistory","No earnings for company","Alert",f"DM_S_SYMB={row[3]}")]
            df.write.mode("append").insertInto("DImessages")   
    
def inc_FactWatches(batch_id): 
        
    data=  pd.read_csv(os.getcwd() + "/data/SF"+str(SF) +"/Batch"+str(batch_id) +"/WatchHistory.txt", header=None,sep=r'[,|]')
    sch = spark.sql("select * from FactWatches").schema

    for index, row in data[0:100].iterrows():
        working_df = []
        # SK_CUSTOMERID and SK_SECURITYID: slighly different (added "IsCurrent=1").
        # Put in as a comment as this is how it was done in FactWatches's historical load
        SK_CUSTOMERID = 0 #spark.sql("select SK_CustomerID from DimCustomer where CUSTOMERID = '" + row[0] + "'AND IsCurrent = 1")
        SK_SECURITYID = 0 #spark.sql("select SK_SecurityID from DimSecurity where SYMBOL = '" + row[1] + "'AND IsCurrent = 1")
        SK_DATEID_DATEPLACED=row[2]
        if row[3]=="ACTV":
            SK_DATEID_DATEREMOVED = ''
        else:
            SK_DATEID_DATEREMOVED = row[2]
        

        working_df = [Decimal(SK_CUSTOMERID),Decimal(SK_SECURITYID), Decimal(SK_DATEID_DATEPLACED),
                        Decimal(SK_DATEID_DATEREMOVED),Decimal(batch_id)]
        df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
        df.write.mode("append").insertInto("FactWatches")
        
    
    
def inc_Prospect(batch_id):
    print("start Prospect")
    prospect_count = 0 

        
    data=pd.read_csv(os.getcwd() + "/data/SF"+str(SF) +"/Batch"+str(batch_id) +"/Prospect.csv", header=None,sep=r'[,|]')
    sch = spark.sql("select * from Prospect").schema

    for index, row in data[0:100].iterrows():
        working_df=[]
        
        # DImessages
        prospect_count += 1
        
        isCustomer = spark.sql("select * from DimCustomer where status = 'ACTIVE' ")
        if isCustomer.count() == 0:
            isCustomer = True
        else:
            isCustomer = False
        SK_RecordDateID = 0 
        SK_UpdateDateID = 0
        
        MarketingNameplate = ""
        if row[12] > 200000 or row[21] > 1000000:
            MarketingNameplate += "+HighValue"
        if row[14] > 3 or row[20] > 5:
            MarketingNameplate += "+Expenses"
        if row[16] > 45:
            MarketingNameplate += "+Boomer"
        if row[12] < 100000 or row[21] < 50000 or row[17] < 600:
            MarketingNameplate += "+MoneyAlert"
        if row[13] > 3 or row[20] > 7 :
            MarketingNameplate += "+Spender"
        if row[16] < 25 and row[12] > 1000000 :
            MarketingNameplate += "+Inherited"
        if len(MarketingNameplate) != 0:
            MarketingNameplate = MarketingNameplate[1:]
        
        
        working_df = [row[0],Decimal(SK_RecordDateID),Decimal(SK_UpdateDateID),
        Decimal(batch_id),isCustomer,row[1],row[2],row[3],row[4],row[5],row[6],
        row[7],row[8],row[9],row[10],
        row[11],Decimal(row[12]),Decimal(row[13]),Decimal(row[14]),row[15],
        Decimal(row[16]),Decimal(row[17]),row[18],row[19],Decimal(row[20]),
        Decimal(row[21]),MarketingNameplate]
        df = spark.createDataFrame(data=[tuple(working_df)],schema=sch)
        #df.write.mode("append").insertInto("Prospect")
        
    # To simulate an update, we want to erase values with batch_id=1 (incremental
    # 1) or batch_id=2 (incremental 2) that meet the following condition:
    # AgencyID is present two times
    """
    input_query = f"
    DELETE FROM Prospect
    WHERE AgencyID NOT IN
    (
        SELECT AgencyID
        FROM Prospect
        GROUP BY AgencyID
        HAVING count(*) = 2
    )
    AND BatchID = {batch_id-1}
    "
    spark.sql(input_query)
    """

    # DImessages
    #df = [(current_timestamp(),batch_id,"Prospect","Source rows","Status",prospect_count)]
    #df.write.mode("append").insertInto("DImessages")
    #df = [(current_timestamp()batch_id,"Prospect","Inserted rows","Status",123)]
    #df.write.mode("append").insertInto("DImessages")
    #df = [(current_timestamp(),batch_id,"Prospect","Updated rows","Status",123)]
    #df.write.mode("append").insertInto("DImessages")
        



In [ ]:
# Start record the time for the incremental load batch 2
start_time_incr_batch2 = time.time()

In [ ]:
incr_DimAccount(2)
incr_DimCustomer(2)
inc_FactCashBalance(2)
#inc_DimTrade(2)
inc_FactHoldings(2)
inc_FactMarketHistory(2)
inc_FactWatches(2) 
inc_Prospect(2)

In [ ]:
# Record the end time for the incremental load batch 2
end_time_incr_batch2 = time.time()
time_incr_batch2 = end_time_incr_batch2 - start_time_incr_batch2

In [ ]:

# Start record the time for the incremental load batch 3
start_time_incr_batch3 = time.time()

In [ ]:
incr_DimAccount(3)
incr_DimCustomer(3)
inc_FactCashBalance(3)
#inc_DimTrade(3)
inc_FactHoldings(3)
inc_FactMarketHistory(3)
inc_FactWatches(3)
inc_Prospect(3)

In [ ]:
# Record the end time for the incremental load batch 3
end_time_incr_batch3 = time.time()
time_incr_batch3 = end_time_incr_batch3 - start_time_incr_batch3

# Automated Audit Phase

In [ ]:
"""
# The following line execute the data visibility query 1. It has to be executed once at the start of the Automated Audit Phase
#spark.sql(os.getcwd() + "/data/output/tpcdi_visibility_1.sql")

f = open(os.getcwd() + "/tpcdi_visibility_1.sql", "r")
tables=f.read()
tables = tables.split(";")[:-1]
for i in tables:
    spark.sql(i)

# Then the audit query has to be runned once
#spark.sql(os.getcwd() + "/data/output/tpcdi_audit.sql")

f = open(os.getcwd() + "/tpcdi_audit.sql", "r")
tables=f.read()
tables = tables.split(";")[:-1]
for i in tables:
    spark.sql(i)
"""

In [ ]:
spark.stop()

## Executions time

In [ ]:
print("Preparation Phase: " + str(preparation_time))
print("Historical Load: " + str(time_histo))
print("Incremental Load Batch 2: " + str(time_incr_batch2))
print("Incremental Load Batch 3: " + str(time_incr_batch3))
print("Total Execution Time: " + str(preparation_time + time_histo + time_incr_batch2 + time_incr_batch3))


labels = ['Preparation Phase', 'Historical Load', 'Incremental Load B2', 'Incremental Load B3']
execution_times = [preparation_time, time_histo, time_incr_batch2, time_incr_batch3]

plt.bar(labels, execution_times, color=['red', 'blue', 'orange', 'green'])
plt.ylabel('Execution Time (seconds)')
plt.title('Comparison of Execution Times')
plt.show()

# After Automated Audit (metric computation)

In [ ]:
# In TPC-DI the times are given as output of the Batch Validation query,
# so we need to retreive them from DImessages table

# CT = Completion Timestamp
CT0 = spark.sql(
    "select MessageDateAndTime from DImessages where BatchID = 0 and MessageType = ‘PCR’"
)
CT1 = spark.sql(
    "select MessageDateAndTime from DImessages where BatchID = 1 and MessageType = ‘PCR’"
)
CT2 = spark.sql(
    "select MessageDateAndTime from DImessages where BatchID = 2 and MessageType = ‘PCR’"
)
CT3 = spark.sql(
    "select MessageDateAndTime from DImessages where BatchID = 3 and MessageType = ‘PCR’"
)

# TH = Throughput of Historical Load
# TH = RH / EH
# --> RH = Row count of Batch1 (from "digen_report.txt")
# --> EH = Elapsed time for Historical Load
TH = 7804509 / (CT1 - CT0)

# For incremental phases, similar to what did before, except that
# the denominator is the maximum betweeen the elapsed time and 1800
TI1 = 33380 / max(CT2 - CT1, 1800)
TI2 = 33455 / max(CT3 - CT2, 1800)

TPC_DI_RPS = round(gmean([TH, min(TI1, TI2)]))